# Beach profile classifier
This notebook is a set of functions that tries to pick a dune crest and dune toe given a beach profile.

## Setup notebook

In [ ]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [ ]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os
import decimal
import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
from plotly import tools
import plotly.io as pio
from scipy import stats
import math
import matplotlib
from matplotlib import cm
import colorlover as cl
import numpy.ma as ma

from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML

from sklearn.metrics import confusion_matrix

import numpy as np
from matplotlib import pyplot as plt

from sklearn import linear_model, datasets

from scipy.interpolate import UnivariateSpline
from scipy.interpolate import interp1d
from scipy.interpolate import splrep, splev
from scipy.integrate import simps
from scipy.stats import linregress
from scipy.signal import find_peaks
import json

In [ ]:
# Matplot lib default settings
plt.rcParams["figure.figsize"] = (10,3)
plt.rcParams['axes.grid']=True
plt.rcParams['grid.alpha'] = 0.5
plt.rcParams['grid.color'] = "grey"
plt.rcParams['grid.linestyle'] = "--"

## Import data
Let's first import data from our pre-processed interim data folder.

In [ ]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_waves = df_from_csv('waves.csv', index_col=[0, 1])
df_tides = df_from_csv('tides.csv', index_col=[0, 1])
df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_sites = df_from_csv('sites.csv', index_col=[0])
df_profile_features_crest_toes = df_from_csv('profile_features_crest_toes.csv', index_col=[0,1])

# Note that the forecasted data sets should be in the same order for impacts and twls
impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }


twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}
print('Done!')

# Implement algorithm

## Get profile data

In [ ]:
def get_profile_data(site, profile_type, df_profiles):
    """
    Returns a list of x and z coordinates for a given site and profile_type from our list of profiles
    """

    # Get x and z coorindates of profile
    x = df_profiles.loc[(site, profile_type)].index.values
    z = df_profiles.loc[(site, profile_type)].z.values

    # Remove nan values
    m = ma.masked_invalid(z)
    x = x[~m.mask]
    z = z[~m.mask]

    #     # Remove landwards of landlim
    #     land_lim = df_profiles.loc[(site, 'poststorm')].land_lim.loc[0]
    #     mask = ma.masked_where(x < land_lim, x)
    #     x = x[~mask.mask]
    #     z = z[~mask.mask]

    return x, z


site = 'NARRA0001'
profile_type = 'prestorm'
x, z = get_profile_data(site, profile_type, df_profiles)

print('x = {} ...'.format(x[0:5]))
print('z = {} ...'.format(z[0:5]))

## Fit linear interpolated spline to profile
- Linear interpolated spline used to simplify the profile. Probably not necessary for picking dune crests/toes, but handy to simplify the profile into a list of linear lines. This helps pick up berms (for later).
- Need to do a bit of optimization to calculate the best smoothing parameter for the profile.

In [ ]:
%matplotlib inline

def pretty_print(l):
    print(json.dumps(l, indent=2, sort_keys=True))

def pairwise(iterable):
    "s -> (s0,s1), (s1,s2), (s2, s3), ..."
    a, b = itertools.tee(iterable)
    next(b, None)
    return zip(a, b)


def xz(x_start, x_end, x, z):
    """
    Returns a list of x coordinates and z coorindates which lie between x_start and x_end
    """
    x_seg = [val for val in x if x_start <= val <= x_end]
    z_seg = [z_val for x_val, z_val in zip(x, z) if x_start <= x_val <= x_end]
    return x_seg, z_seg


def get_slope(x, z):
    slope, intercept, r_value, p_value, std_err = linregress(x, z)
    return slope


def get_r_squared(x, z):
    slope, intercept, r_value, p_value, std_err = linregress(x, z)
    return r_value**2


def rolling_std(a, w):
    """
    Calculates a rolling window standard deviation
    https://stackoverflow.com/a/40773366
    """
    a = np.array(a)
    nrows = a.size - w + 1
    n = a.strides[0]
    a2D = np.lib.stride_tricks.as_strided(a, shape=(nrows, w), strides=(n, n))
    return np.std(a2D, 1)


def iterate_over_smoothing_params(x, z):
    """
    Finds the best smoothing parameter for a linear interpolated spline. 
    Checks a number of smoothing factors, and then tries to minimize the 
    number of knots (changepoints) while retaining decent match to the 
    original profile.
    """

    # Store the results of our iterations in a list of dictionaries
    results = []

    # Iterate through different value of smoothing parameters
    s_vals = [x for x in np.arange(0, 10, 0.01)]

    r2_vals = []
    n_knots = []
    s_vals_to_keep = []

    # Iterate backwards just to make further calcultions more easier.
    for s_val in s_vals[::-1]:

        # Fit spline to profile using the s_val for this iteration
        # k=1 is used to force linear line segments between knots
        s = UnivariateSpline(x, z, s=s_val, k=1)
        xs = np.linspace(x[0], x[-1], 1000)
        zs = s(xs)

        # Find knots
        x_knots = s.get_knots()
        z_knots = s(x_knots)

        # Get number of knots
        n = len(s.get_knots())

        # If we've already recorded data about this number of knots, just skip.
        # Need to also, only have increasing results for spline interpolation
        if n in [x['n'] for x in results
                 ] or n < max([x['n'] for x in results], default=0):
            continue

        # Get r2, how well does the simplification fit the original profile?
        # Create interp model from the knots at our original points.
        f = interp1d(x_knots, z_knots)
        z_lin = f(x)
        r2 = get_r_squared(z, z_lin)

        results.append({'n': n, 's': s_val, 'r2': r2})
    return results


def find_best_smoothing_param(results, min_std=0.0002):
    """
    Given a list of smoothing parameters and their fits, determine what the best smoothing parameter is.
    Larger min_std = more smoothing
    """

    # Get the 2nd derivate of the n_knots vs r2_vals.
    y_spl = UnivariateSpline([x['n'] for x in results],
                             [x['r2'] for x in results],
                             s=0)
    y_spl_2d = y_spl.derivative(n=2)
    y_spl_2d_vals = y_spl_2d([x['n'] for x in results])

    # Get a rolling standard deviation of the derivative
    std = rolling_std(y_spl_2d_vals, w=3)

    # Best smoothing parameter will be when the standard deviation stops changing
    best_i = np.argmax(std < min_std)
    best_s = results[best_i]['s']
    return best_s


def simplify_profile(x, z, site):
    results = iterate_over_smoothing_params(x, z)
    best_s = find_best_smoothing_param(results)

    # Fit spline to profile
    s = UnivariateSpline(x, z, s=best_s, k=1)
    xs = np.linspace(x[0], x[-1], 1000)
    zs = s(xs)

    # Find knots
    x_knots = s.get_knots()
    z_knots = s(x_knots)

#     # Plot for checking
#     plt.title('{}: Linear spline simplification'.format(site))
#     plt.xlabel('Distance (m)')
#     plt.ylabel('Elevation (m AHD)')
#     plt.plot(x, z, 'k.-', label='Raw profile')
#     plt.plot(
#         xs, zs, 'r-', label='Interpolated profile (s={:.2f})'.format(best_s))
#     plt.plot(
#         x_knots,
#         z_knots,
#         'ro',
#         markersize=8,
#         markeredgewidth=1.5,
#         markeredgecolor='orange',
#         label='Interpolated knots (n={})'.format(len(x_knots)))
#     plt.legend(loc='best')
#     plt.show()

    return x_knots, z_knots, best_s


x_knots, z_knots, best_s = simplify_profile(x, z, site)

In [ ]:
%matplotlib inline

def get_x_z_from_knots(x_knots, z_knots):
    # Fit spline to profile
    s = UnivariateSpline(x_knots, z_knots, s=0, k=1)
    xs = np.linspace(x_knots[0], x_knots[-1], 1000)
    zs = s(xs)
    return xs, zs

def simplify_segments_with_same_slopes(x_knots, x, z, site, best_s):
    """
    Removes knots which have similar slopes on either side. 
    This is an extra simplifcation as the linear splines may still include
    some nodes that aren't required.
    """
    removed_x_knots = []
    while True:
        for x_knot1, x_knot2, x_knot3 in zip(x_knots[0:-2], x_knots[1:-1], x_knots[2:]):

            # Get slope of segment behind point at x_knot2
            x_seg, z_seg = xz(x_knot1, x_knot2, x, z)
            slope1 = get_slope(x_seg, z_seg)

            # Get slope of line in front of point at x_knot2
            x_seg, z_seg = xz(x_knot2, x_knot3, x, z)
            slope2 = get_slope(x_seg, z_seg)

            slope_diff = abs(slope1 - slope2)

            # Also check if points are too close together
            if x_knot3 - x_knot1 < 3: # m
                too_close = True
            else:
                too_close = False
            
            # Good, the slopes are different on each side, keep checking
            if slope_diff > 0.01 and too_close == False:
                continue
            # Else bad, slopes are the same so we have to remove this point
            else:
#                 print('Knot at x={} removed (slope_diff={:.3f})'.format(
#                     x_knot2, slope_diff))
                x_knots = np.delete(x_knots, np.where(x_knots == x_knot2), axis=0)
                removed_x_knots.append(x_knot2)
                break

        else:
#             print("All segments have different slopes")
            x_knots_simplified = x_knots
            z_knots_simplified = [
                z_val for x_val, z_val in zip(x, z) if x_val in x_knots_simplified
            ]
            break
    
    # Find z location of our removed knots
    removed_z_knots = [
                z_val for x_val, z_val in zip(x, z) if x_val in removed_x_knots
            ]
    
    # Get the new interpolated spline from our simplified knots
    xs, zs = get_x_z_from_knots(x_knots_simplified, z_knots_simplified)
    
    # Plot for checking
#     plt.title('{}: Linear spline simplification by comparing slopes'.format(site))
#     plt.xlabel('Distance (m)')
#     plt.ylabel('Elevation (m AHD)')
#     plt.plot(x, z, 'k.-', label='Raw profile')
#     plt.plot(
#         xs, zs, 'r-', label='Interpolated profile (s={:.2f})'.format(best_s))
#     plt.plot(
#         x_knots_simplified,
#         z_knots_simplified,
#         'ro',
#         markersize=8,
#         markeredgewidth=1.5,
#         markeredgecolor='orange',
#         label='Interpolated knots (n={})'.format(len(x_knots)))
#     plt.plot(
#         removed_x_knots,
#         removed_z_knots,
#         'ro',
#         markersize=10,
#         markeredgewidth=2.5,
#         markerfacecolor="None",
#         markeredgecolor='orange',
#         label='Removed knots (n={})'.format(len(removed_x_knots)))
#     plt.legend(loc='best')
#     plt.show()

    return x_knots_simplified,z_knots_simplified

x_knots, z_knots = simplify_segments_with_same_slopes(x_knots, x, z, site, best_s)
xs, zs = get_x_z_from_knots(x_knots, z_knots)

In [ ]:
%matplotlib inline 

def dunes_from_d1(xx,zz,zz_d1,
                       min_dune_face_slope=0.05,
                       min_dune_slope_prominence=0.00):
    """
    Get peaks by looking at the derivates (slope)
    """

    # Find the peaks in the first derivatives (i.e. peaks in slopes)
    peaks, props = find_peaks(
        zz_d1 * -1,
#         height=min_dune_face_slope,
        height=(None, None),
        width=(None, None),
        prominence=(None, None)
    )
    
#     print(peaks)
#     plt.figure(figsize=(10, 3))
#     plt.plot(xx, zz_d1*-1, label='raw')
#     plt.show()
    
    # If no peaks found, return None
    if len(peaks) == 0:
        print('No dunes from d1')
        return []

    # The peaks we find are going to be near the center of any face.
    # We need to get the left and right bases to get the peaks and crests.
    x_crests = [xx[val] for val in props['left_bases']]
    x_toes = [xx[val] for val in props['right_bases']]
    heights = [val for val in props['peak_heights']]
    x_centers = xx[peaks]
    z_crests = []
    z_toes = []
    dune_face_slopes = []
    dune_heights = []

    # Let's look at each peak we identified.
    for n, (x_crest, x_center, x_toe, height) in enumerate(zip(x_crests, x_centers, 
                                                x_toes,heights)):
        
        # Once the slope reduces to a certain threshold, consider this the crest/toe
        min_slope = height / -4
        
        # Check the land side of the dune face
        # Find locations where slope is greater than our minimum slope
        land_mask = ((x_crest <= xx) & (xx <= x_center))
        land_slope_okay = zz_d1[land_mask] < min_slope
        x_land_slope_okay = xx[land_mask][~land_slope_okay]
        
        # Get last location where slope satisfies the criteria
        if len(x_land_slope_okay) != 0:
            x_crest = x_land_slope_okay[-1]
            x_crests[n] = x_crest
            
        # Get corresponding z_value for crest
        idx_crest = np.where(x_crest == xx)[0]
        z_crest = zz[idx_crest][0]
        z_crests.append(z_crest)

        # Check the sea side of the dune face
        # Find locations where slope is greater than our minimum slope
        sea_mask = ((x_center <= xx) & (xx <= x_toe))
        sea_slope_okay = zz_d1[sea_mask] < min_slope
        x_sea_slope_okay = xx[sea_mask][~sea_slope_okay]
        
        # Get first location where slope satisfies the criteria
        if len(x_sea_slope_okay) != 0:
            x_toe = x_sea_slope_okay[0]
            x_toes[n] = x_toe
            
        # Get corresponding z_value
        idx_toe = np.where(x_toe == xx)[0]
        z_toe = zz[idx_toe][0]
        z_toes.append(z_toe)

        # Recalculate new slope and dune height
        dune_face_slopes.append((z_crest - z_toe) / (x_crest - x_toe))
        dune_heights.append(z_crest - z_toe)

    dunes = [
        {'x_crest': x_crest,
         'x_toe': x_toe,
         'z_crest': z_crest,
         'z_toe': z_toe,
         'dune_face_slope': dune_face_slope,
         'dune_height': dune_height} for x_crest, x_toe,z_crest,z_toe,dune_face_slope,dune_height in zip(x_crests, x_toes,z_crests,z_toes,dune_face_slopes,dune_heights)
    ]

    return dunes
    
def dunes_from_z_max(xx, zz, zz_d1):
    """
    Estimate dune crest by from the maximum elevation of the profile.
    Toe is estimated by based on d1 (slope)
    Works when there is no clearly defined dune, and always gives us a dune
    """
    
    # Get location of maximum elevation. This is the crest
    i_crest = np.argmax(zz)
    x_crest = xx[i_crest]
    z_crest = zz[i_crest]
    
    # Find peaks in slope seaward of the slope
    peaks, props = find_peaks(
        zz_d1 * -1,
        height=0,
        width=0,
        prominence=0)
    
    # Check which peaks are landward of the crest.
    # Use right base of peak prominence since we want the toe (seaward side of the dune face)
    mask = [True if x > i_crest else False for x in peaks]
    i_seaward_slope_peaks = peaks[mask]
    i_right_bases = props['right_bases'][mask]
    heights = props['peak_heights'][mask]
                             
    if len(i_seaward_slope_peaks) != 0:
        i_seaward_slope_peak = i_seaward_slope_peaks[0]
        i_right_base = i_right_bases[0]
        height = heights[0]
        
        x_center = xx[i_seaward_slope_peak]
        x_toe = xx[i_right_base]
        z_toe = zz[i_right_base]
        
        # Once the slope reduces to a certain threshold, consider this the /toe
        min_slope = height / -4
        
        # Check the sea side of the dune face
        # Find locations where slope is greater than our minimum slope
        sea_mask = ((x_center <= xx) & (xx <= x_toe))
        sea_slope_okay = zz_d1[sea_mask] < min_slope
        x_sea_slope_okay = xx[sea_mask][~sea_slope_okay]
        
        # Get first location where slope satisfies the criteria
        if len(x_sea_slope_okay) != 0:
            x_toe = x_sea_slope_okay[0]
            
        # Get corresponding z_value
        idx_toe = np.where(x_toe == xx)[0]
        z_toe = zz[idx_toe][0]
                
        dune_face_slope = (z_crest - z_toe) / (x_crest - x_toe)
        dune_height = z_crest - z_toe           

    else:
        # No peaks were found...
        
        # Find position of maximum slope seaward of crest
        min_seaward_slope = np.min(zz_d1[i_crest:])
        i_min_seaward_slope = np.argmin(zz_d1[i_crest:])

        # Check if this slope reduces from a certain threshold
        min_threshold_slope = min_seaward_slope / 6

        i_possible_toes = np.where(zz_d1[i_min_seaward_slope:] < min_threshold_slope)

        if len(i_possible_toes) != 0:
            x_toe = xx[i_min_seaward_slope:][i_possible_toes][0]
            z_toe = zz[i_min_seaward_slope:][i_possible_toes][0]
            dune_face_slope = (z_crest - z_toe) / (x_crest - x_toe)
            dune_height = z_crest - z_toe
        else:
            x_toe = np.nan
            z_toe = np.nan
            dune_face_slope = np.nan
            dune_height = np.nan
    
    return [{'x_crest': x_crest,
             'x_toe': x_toe,
             'z_crest': z_crest,
             'z_toe': z_toe,
             'dune_face_slope': dune_face_slope,
             'dune_height': dune_height}]
    
def find_crest_and_toes(x, z, x_knots, best_s):

    # Get a cubic spline so we can have continuous second order deriviates for our profile
    spl = splrep(x, z, k=3, s=best_s)

    # Sample interpolated spline and calcualte derivaives.
    xx = np.linspace(x[0], x[-1], 1000)
    zz = splev(xx, spl)
    zz_d1 = splev(xx, spl, der=1)
    zz_d2 = splev(xx, spl, der=2)
    zz_d3 = splev(xx, spl, der=3)

    # Get potential dunes from different methods
    dunes_d1 = dunes_from_d1(xx,zz,zz_d1,
                                         min_dune_face_slope=0.15,
                                         min_dune_slope_prominence=0.15)
    # Dunes from maximum elevation
    dunes_z_max = dunes_from_z_max(xx, zz, zz_d1)

    # Join list of all potential dunes
    dunes = dunes_d1 + dunes_z_max
    
    # Remove dunes which have the same crest and toe x location
    dunes = [x  for x in dunes if x['x_crest']!=x['x_toe']]
    
    # Calculate area under d1 curve. This'll give an indication of how important the slope is
    for dune in dunes:
        mask = [True if (dune['x_crest'] < x_val) and (x_val < dune['x_toe']) else False for x_val in xx]
        x_seg = xx[mask]
        zz_d1_seg = zz_d1[mask]
        d1_area = simps(zz_d1_seg, x_seg)
        dune['d1_area'] = d1_area

    # Create a filtered flag for all our dunes
    dunes = [dict(item, **{'filtered':False}) for item in dunes]

    # Iterate through each potential dune and decide whether to filter or not
    for dune in dunes:
        
        if dune['z_crest'] < np.median(zz)/2:
            dune['filtered'] = True
            
        elif dune['dune_height'] < 0.5: # m
            dune['filtered'] = True
    
        # Filter out dunes which occur landward of the highest elevation point
    
    
        # TODO Decide to remove the dune toe
        # If mean slope and std between dune toe and dune crests is similar to between dune crest and end of profile,
        # We can remove the toe
        
        
        
#     pretty_print(dunes)
    return xx, zz, zz_d1, zz_d2, zz_d3, dunes



def plot_profile(site, x, z, xx, zz, zz_d1, zz_d2, zz_d3, dunes):
    
    plt.figure(figsize=(10, 12))
    plt.subplot(411)
    plt.plot(x, z, label='raw')
    plt.plot(xx, zz, label='interpolated')
    plt.plot(
        [x['x_crest'] for x in dunes if x['filtered']==True],
        [x['z_crest'] for x in dunes if x['filtered']==True],
        'rv',
        markersize=10,
        fillstyle='none',
        label='Dune crest (potential)')
    plt.plot(
        [x['x_toe'] for x in dunes if x['filtered']==True],
        [x['z_toe'] for x in dunes if x['filtered']==True],
        'r^',
        markersize=10,
        fillstyle='none',
        label='Dune toe (potential)')
    plt.plot(
        [x['x_crest'] for x in dunes if x['filtered']==False],
        [x['z_crest'] for x in dunes if x['filtered']==False],
        'rv',
        markersize=10,
#         label='Dune crest (x={:.2f} m, z={:.2f} m)'.format(x_crest, z_crest)
    )
    plt.plot(
        [x['x_toe'] for x in dunes if x['filtered']==False],
        [x['z_toe'] for x in dunes if x['filtered']==False],
        'r^',
        markersize=10,
#         label='Dune toe (x={:.2f} m, z={:.2f} m)'.format(x_toe, z_toe)
    )
    plt.title('{}: elevations'.format(site))
    plt.legend(loc='best')

    plt.subplot(412)
    d1 = np.diff(zz) / np.diff(xx)
    plt.plot(xx, zz_d1)
#     plt.axvline(x_crest, color='red', label='Dune crest')
#     plt.axvline(x_toe, color='red', label='Dune toe')
    # plt.ylim([-0.2,0.2])
    plt.title('first derivative - slope')

    plt.subplot(413)
    d2 = np.diff(d1) / np.diff(xx[1:])
    plt.plot(xx, zz_d2)
#     plt.axvline(x_crest, color='red', label='Dune crest')
#     plt.axvline(x_toe, color='red', label='Dune toe')
    plt.title('second derivative - change in slope')
    #     plt.ylim([-0.025,0.025])

    plt.subplot(414)
    plt.plot(xx, zz_d3)
#     plt.axvline(x_crest, color='red', label='Dune crest')
#     plt.axvline(x_toe, color='red', label='Dune toe')
    plt.title('third derivative')
    #     plt.ylim([-0.0025,0.0025])

    plt.tight_layout()
    plt.show()


xx, zz, zz_d1, zz_d2, zz_d3, dunes = find_crest_and_toes(x,z,x_knots,best_s)

plot_profile(site, x,z, xx, zz, zz_d1, zz_d2, zz_d3, dunes)

In [ ]:
%matplotlib inline

def get_crests_and_toes(site, profile_type, df_profiles, debug_plot=False):
    x, z = get_profile_data(site, profile_type, df_profiles)
    x_knots, z_knots, best_s = simplify_profile(x, z, site)
    x_knots, z_knots = simplify_segments_with_same_slopes(x_knots, x, z, site, best_s)
    xx, zz, zz_d1, zz_d2, zz_d3, dunes = find_crest_and_toes(x,z,x_knots,best_s)

    if debug_plot:
        plot_profile(site, x,z, xx, zz, zz_d1, zz_d2, zz_d3, dunes)
    
    profile_data = {
        'site': site,
        'profile_type': profile_type,
        'xx': xx,
        'zz': zz,
        'zz_d1': zz_d1,
        'zz_d2': zz_d2,
        'zz_d3': zz_d3,
        'dunes': dunes,
        'x': x,
        'z': z
    }
    
    return profile_data
    
    
import random
site = random.sample(df_profiles.index.get_level_values('site_id').unique().tolist(), 1)[0]

print(site)
# site='NINEMs0004'
profile_data = get_crests_and_toes(site,'prestorm', df_profiles, debug_plot=True)

In [ ]:
sites = df_profiles.index.get_level_values('site_id').unique().tolist()[:10]
profile_data = [get_crests_and_toes(site, 'prestorm', df_profiles) for site in sites]


In [ ]:
%matplotlib notebook

def closest_node(node, nodes):
    """
    https://codereview.stackexchange.com/a/28210
    """
    nodes = np.asarray(nodes)
    deltas = nodes - node
    dist_2 = np.einsum('ij,ij->i', deltas, deltas)
    return np.argmin(dist_2)

def get_data(i, profile_data):
    site = profile_data[i]['site']
    x = profile_data[i]['x']
    z = profile_data[i]['z']
    xx = profile_data[i]['xx']
    zz = profile_data[i]['zz']
    zz_d1 = profile_data[i]['zz_d1']
    zz_d2 = profile_data[i]['zz_d2']
    zz_d3 = profile_data[i]['zz_d3']
    dunes = profile_data[i]['dunes']
    
    return site, x, z, xx, zz,zz_d1,zz_d2,zz_d3, dunes

i = 0
site, x, z, xx, zz,zz_d1,zz_d2,zz_d3, dunes = get_data(i, profile_data)

fig =plt.figure(figsize=(10, 9))
ax1 = plt.subplot(311)
line_xz, = plt.plot(x, z, label='raw')
line_xxzz, = plt.plot(xx, zz, label='interpolated')
pts_filtered_crests, = plt.plot(
    [x['x_crest'] for x in dunes if x['filtered']==True],
    [x['z_crest'] for x in dunes if x['filtered']==True],
    'rv',
    markersize=10,
    fillstyle='none',
    label='Dune crest (filtered)')
pts_filtered_toes, = plt.plot(
    [x['x_toe'] for x in dunes if x['filtered']==True],
    [x['z_toe'] for x in dunes if x['filtered']==True],
    'r^',
    markersize=10,
    fillstyle='none',
    label='Dune toe (filtered)')
pts_potential_crests, = plt.plot(
    [x['x_crest'] for x in dunes if x['filtered']==False],
    [x['z_crest'] for x in dunes if x['filtered']==False],
    'rv',
    markersize=10,
    label='Dune crests (potential)',
)
pts_potential_toes, = plt.plot(
    [x['x_toe'] for x in dunes if x['filtered']==False],
    [x['z_toe'] for x in dunes if x['filtered']==False],
    'r^',
    markersize=10,
    label='Dune toes (potential)',
)
plt.title('{}: elevations'.format(site))
plt.legend(loc='best')

plt.subplot(312)
d1 = np.diff(zz) / np.diff(xx)
plt.plot(xx, zz_d1)
plt.title('first derivative - slope')

plt.subplot(313)
d2 = np.diff(d1) / np.diff(xx[1:])
plt.plot(xx, zz_d2)
plt.title('second derivative - change in slope')
plt.tight_layout()
text=ax1.text(0,0, "test", va="bottom", ha="left")

# Get list of potential crests and toes
potential_crests_x = [x['x_crest'] for x in dunes if x['filtered']==False]
potential_crests_z = [x['z_crest'] for x in dunes if x['filtered']==False]
potential_crests = np.array([(x,z) for x,z in zip(potential_crests_x, potential_crests_z)])

potential_toes_x = [x['x_toe'] for x in dunes if x['filtered']==False]
potential_toes_z = [x['z_toe'] for x in dunes if x['filtered']==False]
potential_toes = np.array([(x,z) for x,z in zip(potential_toes_x, potential_toes_z)])

def on_click(event):
    tx = 'button=%d, x=%d, y=%d, xdata=%f, ydata=%f' % (event.button, event.x, event.y, event.xdata, event.ydata)
    text.set_text(tx)

    # Left click = dune crest
    if event.button == 1:
        i_selected_crest = closest_node(np.array((event.xdata, event.ydata)), potential_crests)
        selected_crest = potential_crests[i_selected_crest]
        tx = 'Selected crest at {}'.format(selected_crest)
        text.set_text(tx)
    
        # Save to data
        
    
    # Right click = dune toe
    if event.button == 3:
        
        if event.xdata > xx[-1]:
            selected_toe = np.nan
            tx = 'Cleared selected toe'
        else:
            i_selected_toe = closest_node(np.array((event.xdata, event.ydata)), potential_crests)
            selected_toe = potential_toes[i_selected_toe]
            tx = 'Selected toe at {}'.format(selected_toe)
        text.set_text(tx)
    
def on_press(event):
    global i
    global potential_crests
    global potential_toes

    if event.key == 'left':
        i = max(0, i-1)
        
    if event.key == 'right':
        i = min(len(profile_data), i+1)
        
#     text.set_text(i)
    site, x, z, xx, zz,zz_d1,zz_d2,zz_d3, dunes = get_data(i, profile_data)

    line_xz.set_xdata(x)
    line_xz.set_ydata(z)
    line_xxzz.set_xdata(xx)
    line_xxzz.set_ydata(zz)
    pts_filtered_crests.set_xdata([x['x_crest'] for x in dunes if x['filtered']==True])
    pts_filtered_crests.set_ydata([x['z_crest'] for x in dunes if x['filtered']==True])
    pts_filtered_toes.set_xdata([x['x_toe'] for x in dunes if x['filtered']==True])
    pts_filtered_toes.set_ydata([x['z_toe'] for x in dunes if x['filtered']==True])
    pts_potential_crests.set_xdata([x['x_crest'] for x in dunes if x['filtered']==False])
    pts_potential_crests.set_ydata([x['z_crest'] for x in dunes if x['filtered']==False])
    pts_potential_toes.set_xdata([x['x_toe'] for x in dunes if x['filtered']==False])
    pts_potential_toes.set_ydata([x['z_toe'] for x in dunes if x['filtered']==False])
    
    
    # Get list of potential crests and toes
    potential_crests_x = [x['x_crest'] for x in dunes if x['filtered']==False]
    potential_crests_z = [x['z_crest'] for x in dunes if x['filtered']==False]
    potential_crests = np.array([(x,z) for x,z in zip(potential_crests_x, potential_crests_z)])

    potential_toes_x = [x['x_toe'] for x in dunes if x['filtered']==False]
    potential_toes_z = [x['z_toe'] for x in dunes if x['filtered']==False]
    potential_toes = np.array([(x,z) for x,z in zip(potential_toes_x, potential_toes_z)])
    
    ax1.set_title('{}: elevations'.format(site))
    
    ax1.relim()
    ax1.autoscale_view()
    
fig.canvas.mpl_connect('button_press_event', on_click)
fig.canvas.mpl_connect('key_press_event', on_press)
    



In [ ]:
# Find berms 
for x_knot1, x_knot2, in zip(x_knots[0:-2], x_knots[1:-1]):
    
    # Berms are only located seaward of the dune toe (but sometimes dune toe is undefined, so use dune crest)
    if x_knot1 < x_crest:
        continue
    
    # Get slope of segment
    x_seg, z_seg = xz(x_knot1, x_knot2, x, z)
    slope = get_slope(x_seg, z_seg)
    z_mean = np.mean(z_seg)
    width = x_knot2 - x_knot1
    
    if slope > -0.01:
        print('{:.1f}m wide berm at x={:.1f}m to x={:.1f}m at z={:.1f}m'.format(width, x_knot1, x_knot2, z_mean))

    

In [ ]:
# def reject_outliers(data, m = 5):
#     d = np.abs(data - np.median(data))
#     mdev = np.median(d)
#     s = d/mdev if mdev else 0.
#     return ma.masked_where(s > m, data)

# def hampel(vals_orig, k=7, t0=3):
#     '''
#     vals: pandas series of values from which to remove outliers
#     k: size of window (including the sample; 7 is equal to 3 on either side of value)
#     '''
#     #Make copy so original not edited
#     vals_orig = pd.Series(vals_orig)
#     vals=vals_orig.copy()    
#     #Hampel Filter
#     L= 1.4826
#     rolling_median=vals.rolling(k).median()
#     difference=np.abs(rolling_median-vals)
#     median_abs_deviation=difference.rolling(k).median()
#     threshold= t0 *L * median_abs_deviation
#     outlier_idx=difference>threshold
#     vals[outlier_idx]=np.nan
#     return(vals.tolist())

# # Remove segements where slopes are too high, indicative of a structure
# segments = [xz(x1, x2,x,z) for (x1, x2) in pairwise(x_knots_simplified)]
# slopes = np.array([get_slope(x1,x2) for x1,x2 in segments])
# mask = reject_outliers(np.array(slopes))
# x_knots_filtered = x_knots_simplified[np.append(True,~mask.mask)]
# z_knots_filtered = [z_val for x_val, z_val in zip(x,z) if x_val in x_knots_filtered]



# # Hampel filter based on z values
# mask = ma.masked_invalid(hampel(z_knots_filtered))
# x_knots_filtered = x_knots_filtered[~mask.mask]
# z_knots_filtered = [z_val for x_val, z_val in zip(x,z) if x_val in x_knots_filtered]



# # plt.figure(figsize=(10,5))
# # plt.plot(x_knots_simplified, np.append(slopes[0],slopes), '.-')
# # plt.plot(x_knots_simplified[np.append(True,~mask.mask)], np.append(slopes[~mask.mask][0], slopes[~mask.mask]), '.-')
# # # plt.plot(xs, zs)
# # # plt.plot(x_knots_filtered, z_knots_filtered,'.',markersize=15)
# # plt.show()




# plt.figure(figsize=(10,5))
# plt.plot(x, z, '.-')
# plt.plot(xs, zs)
# plt.plot(x_knots_filtered, z_knots_filtered,'.',markersize=15)
# plt.show()
# z_knots_filtered

## Find dune crests

In [ ]:



def crest_by_deriv_2(z):
    """
    Try get crest elevation by taking the difference in 2nd derivative of elevation.
    """

    z = savgol_filter(z, 15, 3, mode='nearest')
    deriv_2_diff = np.diff(np.gradient(z)) * -1

    # Ensure same size arrays for plotting
    deriv_2_diff = np.insert(deriv_2_diff, 0, deriv_2_diff[0])
    med = np.median(deriv_2_diff)
    std = np.std(deriv_2_diff)
    peaks, peak_props = find_peaks(deriv_2_diff, height=med+std*2, distance=10)
    return peaks, peak_props, deriv_2_diff


def crest_by_elevation_peaks(z, min_dune_prominence=1.0):
    # Try find peaks in elevation
    peaks, peak_props = find_peaks(z, distance=10, prominence=min_dune_prominence)
    return peaks, peak_props


def get_dune_crest(x, z, xs,zs, x_knots, z_knots, site):
   
    peaks, peak_props = crest_by_elevation_peaks(z)
    
    if peaks.size != 0:
        # Choose crest by most landward peak
        x_crest = x[peaks[-1]]
        z_crest = z[peaks[-1]]
    
    # If no peaks in elevation are found, find by maximum second derivative
    else:
        peaks, peak_props, deriv_2_diff = crest_by_deriv_2(z)
        
        plt.title(
            '{}: Difference of 2nd derivative in elevation'.format(site))
        plt.xlabel('Distance (m)')
        plt.ylabel('Diff(2nd Derivative Elevation)')
        plt.plot(x, deriv_2_diff)

               
        if peaks.size!= 0:

            # Choose crest by highest peak in diff of 2nd derivative
            i_best = np.argmax(peak_props['peak_heights'])
            x_crest = x[peaks[i_best]]
            z_crest = z[peaks[i_best]]
            plt.plot(
                x[peaks],
                deriv_2_diff[peaks],
                'o',
                markersize=20,
                fillstyle='none')
            plt.show() 
            
        else:
            plt.show() 
            # If no peaks in diff of 2nd derivative are found, take landward most point
            if peaks.size == 0:
                x_crest = x_knots[0]
                z_crest = z_knots[0]

    # Move crest to closest knot
    idx_crest = min(range(len(x_knots)), key=lambda i: abs(x_knots[i]-x_crest))
    x_crest = x_knots[idx_crest]
    z_crest = z_knots[idx_crest]
    
    # Plot for checking
    plt.title('{}: Find dune crest by peak in diff 2nd deriv'.format(site))
    plt.xlabel('Distance (m)')
    plt.ylabel('Elevation (m AHD)')
    plt.plot(x, z, 'k.-', label='Raw profile')
    plt.plot(
        xs,
        zs,
        'r-',
        label='Interpolated profile (s={:.2f})'.format(best_s))
    plt.plot(
        x_knots,
        z_knots,
        'ro',
        markersize=8,
        markeredgewidth=1.5,
        markeredgecolor='orange',
        label='Interpolated knots (n={})'.format(len(x_knots)))
    plt.plot(
        x_crest,
        z_crest,
        'bv',
        markersize=10,
        label='Dune crest (selected) (x={:.1f}m,z={:.1f}m)'.format(x_crest,z_crest))
    plt.plot(
        x[peaks],
        z[peaks],
        'o',
        markersize=10,
        fillstyle='none',
        label='Dune crest (potential)')

    plt.legend(loc='best')
    plt.show()
        
    return x_crest, z_crest
        
x_crest, z_crest = get_dune_crest(x, z, xs,zs, x_knots, z_knots, site)

In [ ]:
# Get toe by second derivative
def toe_by_deriv_2(z):
    """
    Try get crest elevation by taking the difference in 2nd derivative of elevation.
    """

    z = savgol_filter(z,11, 3, mode='nearest')
    deriv_2_diff = np.diff(np.gradient(z))

    # Ensure same size arrays for plotting
    deriv_2_diff = np.insert(deriv_2_diff, 0, deriv_2_diff[0])
    med = np.median(deriv_2_diff)
    std = np.std(deriv_2_diff)
    peaks, peak_props = find_peaks(deriv_2_diff, height=max(0.01,med+std*3), distance=10)
    return peaks, peak_props, deriv_2_diff

def get_dune_toe(x, z, xs,zs, x_crest,z_crest,x_knots, z_knots, site):
    peaks, peak_props, deriv_2_diff = toe_by_deriv_2(z)

    plt.title('{}: Difference of 2nd derivative in elevation'.format(site))
    plt.xlabel('Distance (m)')
    plt.ylabel('Diff(2nd Derivative Elevation)')
    plt.plot(x, deriv_2_diff)
    
    if peaks.size!= 0:
        
        # Remove peaks which are behind the crest
        # TODO What happens if all peaks are removed?
        mask = ma.masked_where(x[peaks] <= x_crest, x[peaks])
        peaks = peaks[~mask.mask]

    if peaks.size!= 0:
        # Choose toe by highest peak in diff of 2nd derivative
        i_best = np.argmax(peak_props['peak_heights'])
        x_toe = x[peaks[i_best]][0]
        z_toe = z[peaks[i_best]][0]
#         # Move crest to closest knot
#         idx_toe = min(range(len(x_knots)), key=lambda i: abs(x_knots[i]-x_toe))
#         x_toe = x_knots[idx_toe]
#         z_toe = z_knots[idx_toe]

        plt.plot(
            x[peaks],
            deriv_2_diff[peaks],
            'o',
            markersize=20,
            fillstyle='none')
        plt.show()
    else:
        x_toe = np.nan
        z_toe = np.nan
        plt.show()

    # Plot for checking
    plt.title('{}: Find dune crest by peak in diff 2nd deriv'.format(site))
    plt.xlabel('Distance (m)')
    plt.ylabel('Elevation (m AHD)')
    plt.plot(x, z, 'k.-', label='Raw profile')
    plt.plot(
        xs,
        zs,
        'r-',
        label='Interpolated profile (s={:.2f})'.format(best_s))
    plt.plot(
        x_knots,
        z_knots,
        'ro',
        markersize=8,
        markeredgewidth=1.5,
        markeredgecolor='orange',
        label='Interpolated knots (n={})'.format(len(x_knots)))
    plt.plot(
        x_crest,
        z_crest,
        'bv',
        markersize=10,
        label='Dune crest(x={:.1f} m,z={:.1f} m)'.format(x_crest,z_crest))
    plt.plot(
        x_toe,
        z_toe,
        'b^',
        markersize=10,
        label='Dune toe (x={:.1f} m,z={:.1f} m)'.format(x_toe,z_toe))

    plt.legend(loc='best')
    plt.show()
    return x_toe, z_toe
x_toe, z_toe = get_dune_toe(x, z, xs,zs, x_crest,z_crest,x_knots, z_knots, site)

In [ ]:
def find_dune_crest_and_toe(site, profile_type, df_profiles):
    x, z = get_profile_data(site, profile_type, df_profiles)
    x_knots, z_knots = simplify_profile(x, z, site)
    x_knots, z_knots = simplify_segments_with_same_slopes(x_knots, x, z, site)
    xs, zs = get_x_z_from_knots(x_knots, z_knots)
    x_crest, z_crest = get_dune_crest(x, z, xs,zs, x_knots, z_knots, site)
    x_toe, z_toe = get_dune_toe(x, z, xs,zs, x_crest,z_crest,x_knots, z_knots, site)
    
find_dune_crest_and_toe('ENTRA0004', 'prestorm', df_profiles)
